### Setup

In [1]:
try:
    import google.colab
    IN_COLAB = True
    %pip install sae-lens transformer-lens

    from google.colab import drive
    drive.mount('/content/drive')
except ImportError:
    IN_COLAB = False

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 50.4/50.4 kB 2.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 143.1/143.1 kB 10.3 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 123.7/123.7 kB 10.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 920.0/920.0 kB 52.4 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 175.6/175.6 kB 16.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 57.7/57.7 kB 5.3 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 739.7/739.7 kB 48.5 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 527.3/527.3 kB 34.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 42.4/42.4 kB 3.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 8.3/8.3 MB 39.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 12.8/12.8 MB 87.6 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.4/5.4 MB 84.6 MB/s eta 0:00:00
  

In [2]:
# Standard imports
import os
import numpy as np
from tqdm import tqdm
import plotly.express as px
import pandas as pd
import einops
from datasets import load_dataset
from sae_lens import SAE, HookedSAETransformer
from transformers import AutoModelForCausalLM, AutoTokenizer, BitsAndBytesConfig
from sae_lens import LanguageModelSAERunnerConfig
from sae_lens import ActivationsStore
import os
from dotenv import load_dotenv
import typing
from dataclasses import dataclass
from tqdm import tqdm
import logging
import torch
import torch.nn.functional as F

# GPU memory saver (this script doesn't need gradients computation)
torch.set_grad_enabled(False)

### Config

In [3]:
# define the model to work with
MODEL = 'GPT2' # GEMMA, MISTRAL, GPT2

if MODEL == 'GEMMA':
    # Base model stuff
    BASE_MODEL = "google/gemma-2b"
    DATASET_NAME = "ctigges/openwebtext-gemma-1024-cl"
    BASE_TOKENIZER_NAME = BASE_MODEL

    # Finetuned model stuff
    FINETUNE_MODEL = 'shahdishank/gemma-2b-it-finetune-python-codes'
    FINETUNE_PATH = None

    # SAE stuff
    RELEASE = 'gemma-2b-res-jb'
    hook_part = 'post'
    layer_num = 6
elif MODEL == 'MISTRAL':
    # Base model stuff
    BASE_MODEL = "mistral-7b"
    DATASET_NAME = "monology/pile-uncopyrighted"
    BASE_TOKENIZER_NAME = 'mistralai/Mistral-7B-v0.1'

    # Finetuned model stuff
    FINETUNE_MODEL = 'meta-math/MetaMath-Mistral-7B'
    FINETUNE_PATH = f'/content/drive/My Drive/Finetunes/MetaMath-Mistral-7B'

    # SAE stuff
    RELEASE = 'mistral-7b-res-wg'
    hook_part = 'pre'
    layer_num = 8
elif MODEL == 'GPT2':
    # Base model stuff
    BASE_MODEL = "gpt2-small"
    DATASET_NAME = "Skylion007/openwebtext"
    BASE_TOKENIZER_NAME = 'openai-community/gpt2'

    # Finetuned model stuff
    FINETUNE_MODEL = 'pierreguillou/gpt2-small-portuguese'
    FINETUNE_PATH = None

    # SAE stuff
    RELEASE = 'gpt2-small-res-jb'
    hook_part = 'pre'
    layer_num = 6

saving_name_base = BASE_MODEL if "/" not in BASE_MODEL else BASE_MODEL.split("/")[-1]
saving_name_ft = FINETUNE_MODEL if "/" not in FINETUNE_MODEL else FINETUNE_MODEL.split("/")[-1]
saving_name_ds = DATASET_NAME if "/" not in DATASET_NAME else DATASET_NAME.split("/")[-1]

SAE_HOOK = f'blocks.{layer_num}.hook_resid_{hook_part}'

### Loading the activations

Now we load our tensors from pre_3_compute_activations.ipynb:

In [4]:
from pathlib import Path
def get_base_and_data_paths(drive_folder='My Drive/sae_data'):
    if IN_COLAB:
      return Path('./'), Path(f'/content/drive/{drive_folder}')

    # Load environment variables from the .env file
    load_dotenv()
    # Access the PYTHONPATH variable
    pythonpath = Path(os.getenv('PYTHONPATH'))
    # Print to verify
    print(f"PYTHONPATH: {pythonpath}")
    datapath = pythonpath / 'data'
    print(f"DATAPATH: {datapath}")

    return pythonpath, datapath

_, datapath = get_base_and_data_paths()

import gc
def clear_cache():
    gc.collect()
    torch.cuda.empty_cache()

In [5]:
base_activations = torch.load(datapath / f"base_acts_{saving_name_base}_on_{saving_name_ds}.pt")
finetune_activations = torch.load(datapath / f"finetune_acts_{saving_name_ft}_on_{saving_name_ds}.pt")

base_activations.shape, finetune_activations.shape

<ipython-input-5-3df52977ced4>:1: FutureWarning: You are using `torch.load` with `weights_only=False` (the current default value), which uses the default pickle module implicitly. It is possible to construct malicious pickle data which will execute arbitrary code during unpickling (See https://github.com/pytorch/pytorch/blob/main/SECURITY.md#untrusted-models for more details). In a future release, the default value for `weights_only` will be flipped to `True`. This limits the functions that could be executed during unpickling. Arbitrary objects will no longer be allowed to be loaded via this mode unless they are explicitly allowlisted by the user via `torch.serialization.add_safe_globals`. We recommend you start setting `weights_only=True` for any use case where you don't have full control of the loaded file. Please open an issue on GitHub for any issues related to this experimental feature.
  base_activations = torch.load(datapath / f"base_acts_{saving_name_base}_on_{saving_name_ds}.p

(torch.Size([250, 1024, 768]), torch.Size([250, 1024, 768]))

### Computing the similarities

In [6]:
#### Similarity and Distance Computations ####

# 1. Compute pairwise cosine similarity between base and finetune activations
def compute_cosine_similarity(base_activations, finetune_activations):
    # Normalize activations along the activation dimension
    base_norm = F.normalize(base_activations, dim=-1)
    finetune_norm = F.normalize(finetune_activations, dim=-1)

    # Compute dot product along activation dimension to get cosine similarity
    cosine_similarity = torch.einsum('bca,bca->bc', base_norm, finetune_norm)  # [N_BATCH, N_CONTEXT]
    return cosine_similarity

# 2. Compute pairwise Euclidean distance between base and finetune activations
def compute_euclidean_distance(base_activations, finetune_activations):
    # Compute squared difference and sum along activation dimension
    euclidean_distance = torch.norm(base_activations - finetune_activations, dim=-1)  # [N_BATCH, N_CONTEXT]
    return euclidean_distance

In [7]:
N_CONTEXT = base_activations.shape[1]

In [8]:
# Call the functions to compute cosine similarity and Euclidean distance
cosine_similarity = compute_cosine_similarity(base_activations, finetune_activations)
euclidean_distance = compute_euclidean_distance(base_activations, finetune_activations)

del base_activations, finetune_activations
clear_cache()

# Output tensor shapes
print(f"Cosine Similarity Tensor Shape: {cosine_similarity.shape}")  # [N_BATCH, N_CONTEXT]
print(f"Euclidean Distance Tensor Shape: {euclidean_distance.shape}")  # [N_BATCH, N_CONTEXT]

Cosine Similarity Tensor Shape: torch.Size([250, 1024])
Euclidean Distance Tensor Shape: torch.Size([250, 1024])


### Plotting the similiraties

In [9]:
import plotly.express as px
import plotly.graph_objects as go

In [10]:
# 1. Plot heatmap of similarity metric
def plot_similarity_heatmap(ST):
    fig = px.imshow(ST.cpu().numpy(), color_continuous_scale='Viridis',
                    labels={'x': 'Context (Tokens)', 'y': 'Batch Index'},
                    title="Similarity Heatmap (Batches vs Context)")
    fig.show()

# 2. Reduce ST across context dimension to [N_BATCH] and plot histogram across batches
def plot_batch_histogram(ST):
    batch_mean_similarity = torch.mean(ST, dim=1).cpu().numpy()  # Shape [N_BATCH]
    fig = px.histogram(batch_mean_similarity, nbins=30, labels={'value': 'Mean Similarity'},
                       title="Histogram of Mean Similarity Across Batches")
    fig.show()

# 3. Flatten ST into [N_BATCH * N_CONTEXT] and plot histogram across all tokens
def plot_token_histogram(ST):
    flattened_ST = ST.flatten().cpu().numpy()  # Shape [N_BATCH * N_CONTEXT]
    fig = px.histogram(flattened_ST, nbins=100, labels={'value': 'Similarity'},
                       title="Histogram of Similarity Across All Tokens")
    fig.show()

# 4. Reduce ST across batch dimension to [N_CONTEXT] and plot line plot across context
def plot_context_line(ST):
    context_mean_similarity = torch.mean(ST, dim=0).cpu().numpy()  # Shape [N_CONTEXT]
    fig = go.Figure()
    fig.add_trace(go.Scatter(x=list(range(N_CONTEXT)), y=context_mean_similarity,
                             mode='lines', name='Context Mean Similarity'))
    fig.update_layout(title="Line Plot of Mean Similarity Across Context",
                      xaxis_title="Context (Tokens)", yaxis_title="Mean Similarity")
    fig.show()

# 5. Report the global mean value of the similarity metric
def report_global_mean(ST):
    global_mean_similarity = torch.mean(ST).item()
    print(f"Global mean similarity: {global_mean_similarity}")



In [11]:
ST1 = cosine_similarity
ST2 = euclidean_distance

In [12]:
# Call the functions in sequence
plot_similarity_heatmap(ST1)

In [13]:
plot_batch_histogram(ST1)

In [14]:
plot_token_histogram(ST1)

In [15]:
plot_context_line(ST1)

In [16]:
report_global_mean(ST1)

Global mean similarity: 0.48193359375


In [17]:
plot_similarity_heatmap(ST2)

In [18]:
plot_batch_histogram(ST2)

In [19]:
plot_token_histogram(ST2)

In [20]:
plot_context_line(ST2)

In [21]:
report_global_mean(ST2)

Global mean similarity: 80.375
